In [37]:
import numpy as np
import tensorflow as tf

import plotly.express as px
import plotly.graph_objects as go

from utils import cartesian_product

In [18]:
RECOIL_ENERGY_752 = 1032 # Hz
RECOIL_ENERGY_532 = 2062 # Hz

In [123]:
num_quasimomentum_components = 99

max_momentum_site_component = 7
num_momentum_sites = (2*max_momentum_site_component + 1) ** 2

quasimomentum_component = np.linspace(-2, 2, num_quasimomentum_components)
quasimomentum = cartesian_product(*(quasimomentum_component,)*2)

momentum_site_component = np.arange(-max_momentum_site_component, max_momentum_site_component + 1)
momentum_site = cartesian_product(*(momentum_site_component,)*2)

In [124]:
def render_momentum_site_potential(square_depth, stripe_depth):
    momentum_site_potential = np.zeros((3, 3))

    def add(momentum_site, potential):
        momentum_site_potential[momentum_site[:, 0] + 1, momentum_site[:, 1] + 1] += potential

    add(np.array([[ 0,  0]                              ]), -1/4  * square_depth)
    add(np.array([[-1,  0], [+1,  0], [0,  -1], [ 0, +1]]), -1/8  * square_depth)
    add(np.array([[-1, -1], [-1, +1], [+1, -1], [+1, +1]]), -1/16 * square_depth)

    add(np.array([[ 0,  0]]),           -1/2 * stripe_depth)
    add(np.array([[-1, -1], [+1, +1]]), -1/4 * stripe_depth)

    return momentum_site_potential

In [125]:
def spatial_from_momentum_site_potential(momentum_site_potential, num_points=100):
    spatial_potential = tf.math.real(tf.signal.rfft2d(tf.signal.ifftshift(tf.pad(momentum_site_potential, tf.constant(np.full((2, 2), num_points))))))
    return tf.concat([spatial_potential, tf.reverse(spatial_potential, [0, 1])], 1)

def tile_spatial_potential(spatial_potential, periods=1):
    return tf.tile(spatial_potential, np.full((2,), periods))

In [126]:
def compute_dispersion(momentum_site_potential):
    momentum = 2*momentum_site + quasimomentum[:, np.newaxis]
    kinetic = tf.linalg.diag(np.linalg.norm(momentum, axis=-1) ** 2)

    momentum_site_change = momentum_site[:, np.newaxis] - momentum_site
    max_momentum_site_component_change = 2 * max_momentum_site_component - 1
    momentum_site_to_index = (momentum_site_potential.shape[0] - 1) // 2 
    potential = np.pad(momentum_site_potential, max_momentum_site_component_change)[
        momentum_site_change[:, :, 0] + momentum_site_to_index + max_momentum_site_component_change, 
        momentum_site_change[:, :, 1] + momentum_site_to_index + max_momentum_site_component_change]

    energy = kinetic + potential[np.newaxis, ...]

    dispersion = tf.reshape(tf.linalg.eigvalsh(energy), (num_quasimomentum_components, num_quasimomentum_components, (2*max_momentum_site_component + 1) ** 2))

    return dispersion

In [127]:
def compute_tunneling_strengths(dispersion):
    return tf.signal.fftshift(tf.abs(tf.signal.fft2d(tf.cast(dispersion[:, :, 0], tf.complex64))) / num_quasimomentum_components ** 2)

In [128]:
def compute_neighbor_tunneling_strengths(tunneling_strengths, radius=1):
    index_min = num_quasimomentum_components // 2 - radius
    index_max = num_quasimomentum_components // 2 + radius
    return tunneling_strengths[index_min:index_max+1, index_min:index_max+1]

# Square

In [129]:
momentum_site_potential = render_momentum_site_potential(10, 1)
momentum_site_potential

array([[-0.875, -1.25 , -0.625],
       [-1.25 , -3.   , -1.25 ],
       [-0.625, -1.25 , -0.875]])

In [130]:
spatial_potential = spatial_from_momentum_site_potential(momentum_site_potential)

figure = go.Figure(data=[go.Surface(z=tile_spatial_potential(spatial_potential, 2))])
figure.update_layout(autosize=False, width=750, height=750)
figure.show()

In [131]:
dispersion = compute_dispersion(momentum_site_potential)

figure = go.Figure(data=[go.Surface(x=quasimomentum_component, y=quasimomentum_component, z=dispersion[:, :, 0])])
figure.update_layout(autosize=False, width=750, height=750)
figure.show()

In [121]:
tunneling_strengths = compute_tunneling_strengths(dispersion)
neighbor_tunneling_strengths = compute_neighbor_tunneling_strengths(tunneling_strengths, radius=2)
px.imshow(neighbor_tunneling_strengths, zmax=0.03, width=750, height=750)

In [102]:
tunneling_strengths = compute_tunneling_strengths(dispersion)
neighbor_tunneling_strengths = compute_neighbor_tunneling_strengths(tunneling_strengths, radius=2)
px.imshow(neighbor_tunneling_strengths * RECOIL_ENERGY_752, zmax=31, width=750, height=750)

# Triangle

In [103]:
momentum_site_potential = render_momentum_site_potential(4, 8 * RECOIL_ENERGY_532/RECOIL_ENERGY_752)
momentum_site_potential

array([[-4.24612403, -0.5       , -0.25      ],
       [-0.5       , -8.99224806, -0.5       ],
       [-0.25      , -0.5       , -4.24612403]])

In [104]:
spatial_potential = spatial_from_momentum_site_potential(momentum_site_potential)

figure = go.Figure(data=[go.Surface(z=tile_spatial_potential(spatial_potential, 1))])
figure.update_layout(autosize=False, width=750, height=750)
figure.show()

In [105]:
dispersion = compute_dispersion(momentum_site_potential)

figure = go.Figure(data=[go.Surface(x=quasimomentum_component, y=quasimomentum_component, z=dispersion[:, :, 0])])
figure.update_layout(autosize=False, width=750, height=750)
figure.show()

In [110]:
tunneling_strengths = compute_tunneling_strengths(dispersion)
neighbor_tunneling_strengths = compute_neighbor_tunneling_strengths(tunneling_strengths, radius=2)
print(f"Horizontal/Vertical Tunneling: {neighbor_tunneling_strengths[2][1] * RECOIL_ENERGY_752:.4f}, Diagonal Tunneling: {neighbor_tunneling_strengths[3][1] * RECOIL_ENERGY_752:.4f}")
px.imshow(neighbor_tunneling_strengths * RECOIL_ENERGY_752, zmax=21, width=750, height=750)

Horizontal/Vertical Tunneling: 15.3688, Diagonal Tunneling: 15.8377
